# 测试 `PrintAfterAll` 和 `PrintBeforeAll`

In [1]:
from io import StringIO
from contextlib import redirect_stdout
import tvm
from tvm import relax
from tvm.ir.instrument import PrintAfterAll, PrintBeforeAll
from tvm.script import ir as I
from tvm.script import relax as R
from tvm.script import tir as T

In [2]:
@T.prim_func
def func(a: T.handle, b: T.handle) -> None:
    A = T.match_buffer(a, (128, 128, 128, 128))
    B = T.match_buffer(b, (128, 128, 128, 128))
    for i, j, k, l in T.grid(128, 128, 128, 128):
        with T.block("B"):
            vi, vj, vk, vl = T.axis.remap("SSSS", [i, j, k, l])
            B[vi, vj, vk, vl] = A[vi, vj, vk, vl] * 2.0

with redirect_stdout(StringIO()) as sio:
    with tvm.transform.PassContext(opt_level=3, instruments=[PrintBeforeAll(), PrintAfterAll()]):
        tvm.compile(func)
all_passes_output = sio.getvalue()
assert "Before Running Pass:" in all_passes_output
assert "After Running Pass:" in all_passes_output
assert "pass name: tir." in all_passes_output

In [3]:
@I.ir_module
class Module:
    @R.function
    def func(x: R.Tensor((16,), "float32"), y: R.Tensor((16,), "float32")):
        z = R.add(x, y)
        y = z
        return y

pipeline = relax.get_pipeline("default_build")
with redirect_stdout(StringIO()) as sio:
    with tvm.transform.PassContext(opt_level=3, instruments=[PrintBeforeAll(), PrintAfterAll()]):
        pipeline(Module)
all_passes_output = sio.getvalue()
assert "Before Running Pass:" in all_passes_output
assert "After Running Pass:" in all_passes_output
assert "pass name: _pipeline" in all_passes_output